In [7]:
import requests 
from bs4 import BeautifulSoup 
import pandas as pd

# CID : 카테고리(소설 : 1, 에세이 :55889 , 자기계발 : 336)

items = []
lists = []
results = []
KEY = 'ttbjaylee20090030001'

CID = 517

for page in range(1,494): # 페이지 입력
    print(page)
    
    url = f"https://www.aladin.co.kr/shop/wbrowse.aspx?BrowseTarget=List&ViewRowsCount=50&ViewType=Detail\
    &PublishMonth=0&SortOrder=2&page={page}&Stockstatus=0&PublishDay=84&CustReviewRankStart=0&CustReviewCountStart=0&PriceFilterMax=-1\
    &CID={CID}&SearchOption="
    
    res = requests.get(url) 
    res.raise_for_status() # 정상 200
    soup = BeautifulSoup(res.text, "lxml")
    
    # 페이지에 있는 도서 링크(50개)
    book_links = soup.select('ul > li > a.bo3')
    links = []
    for book_link in book_links:
        a= book_link['href']
        links.append(a)
    for link in links:
        res = requests.get(link)
        soup = BeautifulSoup(res.text, "lxml")
        try:
            ISBN = soup.select('div.conts_info_list1 > ul > li')
            ISBN = ISBN[-1].text[-13:]
        except:
            pass
    
        #data = [ISBN]
        results.append(ISBN)

len(results)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


24625

In [8]:
import pickle
ISBN336_01_51 = pd.DataFrame(results)
ISBN336_01_51.to_pickle('LINK_LIST_74_01_494.plk')

In [9]:
# 링크
url_look_list = []

#API 키 발급
KEY = 'ttbjaylee20090030001' 

# 링크 저장
for isbn in results:
    url_look = 'https://www.aladin.co.kr/ttb/api/ItemLookUp.aspx?ttbkey={}&itemIdType=isbn13&ItemId={}&output=JS&Version=20131101&OptResult=authors,reviewList,fulldescription,fulldescription2,Story,categoryIdList'.format(KEY, isbn)
    url_look_list.append(url_look)
print(url_look_list)


['https://www.aladin.co.kr/ttb/api/ItemLookUp.aspx?ttbkey=ttbjaylee20090030001&itemIdType=isbn13&ItemId=9791168341746&output=JS&Version=20131101&OptResult=authors,reviewList,fulldescription,fulldescription2,Story,categoryIdList', 'https://www.aladin.co.kr/ttb/api/ItemLookUp.aspx?ttbkey=ttbjaylee20090030001&itemIdType=isbn13&ItemId=9791198593276&output=JS&Version=20131101&OptResult=authors,reviewList,fulldescription,fulldescription2,Story,categoryIdList', 'https://www.aladin.co.kr/ttb/api/ItemLookUp.aspx?ttbkey=ttbjaylee20090030001&itemIdType=isbn13&ItemId=9788934972464&output=JS&Version=20131101&OptResult=authors,reviewList,fulldescription,fulldescription2,Story,categoryIdList', 'https://www.aladin.co.kr/ttb/api/ItemLookUp.aspx?ttbkey=ttbjaylee20090030001&itemIdType=isbn13&ItemId=9788934942467&output=JS&Version=20131101&OptResult=authors,reviewList,fulldescription,fulldescription2,Story,categoryIdList', 'https://www.aladin.co.kr/ttb/api/ItemLookUp.aspx?ttbkey=ttbjaylee20090030001&itemI

In [10]:
print(len(url_look_list))

24625


In [11]:
# 저장한 링크에서 책 정보 가져오기
import requests
import pandas as pd
import time

items = []
lists = []

for url_look in url_look_list:
    while True:
        try:
            response = requests.get(url_look)
            response.raise_for_status()  # 오류가 발생하면 예외를 발생

            text = response.json()  # JSON 응답을 파싱

            item = text.get('item', [])  # 'item' 키가 있는 경우 해당 값을 가져옴
            if item:
                # 도서 정보
                title = item[0].get('title', '')
                author = item[0].get('author', '')
                pubDate = item[0].get('pubDate', '')
                description = item[0].get('description', '')
                isbn13 = item[0].get('isbn13', '')
                categoryID = item[0].get('categoryId', '')
                categoryName = item[0].get('categoryName', '')
                salesPoint = item[0].get('salesPoint', '')
                adult = item[0].get('adult', '')
                rank = item[0].get('customerReviewRank', '')
                fullDes = item[0].get('fullDescription', '')
                fullDes2 = item[0].get('fullDescription2', '')
                story = item[0].get('subInfo', {}).get('story', '')

                # 리뷰 정보
                reviewList = item[0].get('reviewList', [])
                if reviewList:
                    reviewrank = reviewList[0].get('reviewRank', 0)
                    reviewtitle = reviewList[0].get('title', 0)
                    review_w = reviewList[0].get('writer', 0)
                else:
                    reviewrank = 0
                    reviewtitle = 0
                    review_w = 0

                # 리스트에 도서 정보를 추가
                lists.append([title, author, pubDate, description, isbn13, categoryID, categoryName,
                            salesPoint, adult, rank, fullDes, fullDes2, story, reviewrank, reviewtitle, review_w])
            time.sleep(0.5)
            break
        except requests.exceptions.RequestException as e:
            print(f"요청 중 오류 발생: {e}")

# 데이터프레임을 생성
cols = ['title', 'author', 'pubDate', 'description', 'isbn13', 'categoryID', 'categoryName',
        'salesPoint', 'adult', 'rank', 'fullDes', 'fullDes2', 'story', 'reviewrank', 'reviewtitle', 'review_w']
df = pd.DataFrame(lists, columns=cols)

import pickle
df.to_pickle('ISBN74_1_493.pkl', protocol=4)
### pkl 이름 ISBN[카테고리 번호]_[페이지 시작]_[페이지 끝] 으로 저장

In [12]:
df

title  \
0           물질의 세계 - 6가지 물질이 그려내는 인류 문명의 대서사시   
1                    요즘 역사 : 근대 - 당신에게 가장 가까운   
2     사피엔스 - 유인원에서 사이보그까지, 인간 역사의 대담하고 위대한 질문   
3                     총 균 쇠 - 인간 사회의 운명을 바꾼 힘   
4     컬처, 문화로 쓴 세계사 - 하버드대 마틴 푸크너의 인류 문화 오디세이   
...                                       ...   
4925               대한국民 현대사 - 국민으로 살아낸 국민의 역사   
4926           스포츠 코리아 판타지 - 스포츠로 읽는 한국 사회문화사   
4927                                   칸의 후예들   
4928                                   해적의 역사   
4929              하늘에 그려진 이야기 - 그리스인들의 별자리 신화   

                                 author     pubDate  \
0               에드 콘웨이 (지은이), 이종인 (옮긴이)  2024-03-08   
1                             황현필 (지은이)  2024-03-26   
2     유발 하라리 (지은이), 조현욱 (옮긴이), 이태수 (감수)  2023-04-01   
3            재레드 다이아몬드 (지은이), 강주헌 (옮긴이)  2023-05-10   
4                마틴 푸크너 (지은이), 허진 (옮긴이)  2024-02-13   
...                                 ...         ...   
4925                          고경태 (지은이)  2013-05-07   
4926                          정희준 (지은이)  2009-02-02   
4927           라시드 앗 딘 (지은이), 김호동 (옮긴이)  2005-11-07   
4928           앵거스 컨스텀 (지은이), 이종인 (옮긴이)  2002-08-27   
4929        데이비드 W. 마셜 (지은이), 이종인 (옮긴이)  2020-02-19   

                                            description         isbn13  \
0     저자이자 영국의 저널리스트 에드 콘웨이는 우리가 알지 못했고 볼 수 없었던 물질이 ...  9791168341746   
1     흥선대원군이 집권을 시작한 1863년부터 대한제국이 일제에 병합된 1910년까지의 ...  9791198593276   
2     2011년 원서 출간 이후 10년을 돌아보고 위기 상황을 맞은 인류에게 건네는 제언...  9788934972464   
3     학문의 경계를 넘나드는 세계적 석학 재레드 다이아몬드. 인류 문명에 대한 예리한 통...  9788934942467   
4     하버드대 마틴 푸크너의 인류 문화 오디세이. 모든 영웅의 원형을 만든 호메로스 서사...  9791167741370   
...                                                 ...            ...   
4925  저자인 아들이 아버지가 20년 전에 남기고 떠난 스크랩북을 펼친다. 처음 접하는 메...  9788971846902   
4926  스포츠로 읽는 한국 사회문화사. 한국사회가 스포츠와 언제부터, 어떻게 서로 영향을 ...  9788957690932   
4927  몽골 세계제국의 출현은 오늘날 우리의 눈에뿐만 아니라 당대인들에게도 놀라운 역사적 ...  9788958281337   
4928  '해적'은 현대사회의 구속을 벗어나고자 하는 이들에게 왠지 모를 낭만적인 이미지로 ...  9788984351226   
4929  별자리에 대한 이야기뿐 아니라 별자리의 그리스어, 라틴어 이름, 주성, 적경, 적위...  9791135438448   

      categoryID               categoryName  salesPoint  adult  rank fullDes  \
0          51378            국내도서>인문학>교양 인문학       33845  False    10           
1          52593             국내도서>역사>한국사 일반       25410  False     9           
2          51545       국내도서>인문학>인류학/고고학>인류학      130773  False     9           
3          51378            국내도서>인문학>교양 인문학       46954  False    10           
4             78                국내도서>역사>고고학       25750  False    10           
...          ...                        ...         ...    ...   ...     ...   
4925       52591  국내도서>역사>한국근현대사>한국전쟁 이후~현재         341  False     6           
4926       52593             국내도서>역사>한국사 일반         341  False     6           
4927        5445        국내도서>역사>아시아사>중앙아시아사         341  False     9           
4928        1806          국내도서>역사>서양사>서양사일반         341  False     6           
4929          94          국내도서>역사>서양사>서양고대사         340  False     8           

     fullDes2 story  reviewrank  reviewtitle  review_w  
0                             0            0         0  
1                             0            0         0  
2                             0            0         0  
3                             0            0         0  
4                             0            0         0  
...       ...   ...         ...          ...       ...  
4925                          0            0         0  
4926                          0            0         0  
4927                          0            0         0  
4928                          0            0         0  
4929                          0            0         0  

[4930 rows x 16 columns]